## Results analysis

In this jupyter notebook I will try to examine why models are making mistakes during classification. To achieve that I have to use code from benchmark.py, select dataset, train model and examine what went wrong. I have used LIME algorithm (**eli5** and **lime** module) to visualize weights assigned to every word and every target class.

In [1]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines) {
    return false;
}

<IPython.core.display.Javascript object>

In [2]:
import argparse
import numpy as np
import pandas as pd
import time
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split

from load_dataset import load_bbc_dataset
from load_dataset import load_news_groups_dataset
from load_dataset import load_yahoo_answers_dataset
from load_dataset import load_ohsumed_dataset
from load_dataset import load_reuters_dataset
from models.tfidf_model import TfIdfModel
from models.doc2vec_model import Doc2VecDBOWModel, Doc2VecDMModel
from models.lda_model import LDAModel
from models.lsa_model import LSAModel
from models.han_model import HANModel
from models.sif_model import SIFModel
from models.cbow_model import CBOWModel

import logging
import multiprocessing
cores = multiprocessing.cpu_count() - 1

parser =  argparse.ArgumentParser(
    description="Benchmark for documents embedding methods")

parser.add_argument("-d",
    "--dataset_path",
    dest="dataset_path",
    required=True,
    help="Path to dataset")

parser.add_argument("-m",
    "--models_path",
    dest="models_path",
    required=True,
    help="Path to models")

parser.add_argument("-p",
    "--pretrained_path",
    dest="pretrained_path",
    required=True,
    help="Path to pretrained embedding model")

parser.add_argument("-n",
    "--dataset_name",
    dest="dataset_name",
    choices=['bbc','yahoo','20newsgroups', 'reuters', 'ohsumed'],
    required=True,
    help="Name of dataset")

parser.add_argument("-r",
    "--restore",
    dest="restore",
    required=False,
    action='store_true',
    help="Path to models")

parser.add_argument("-l",
    "--logging",
    dest="logging",
    required=False,
    help="Path to logging file")

Using TensorFlow backend.


_StoreAction(option_strings=['-l', '--logging'], dest='logging', nargs=None, const=None, default=None, type=None, choices=None, help='Path to logging file', metavar=None)

In [3]:
# args = parser.parse_args("-d datasets/Reuters21578-Apte-90Cat/ -m models/ -p glove/glove.6B.100d.txt -n reuters".split())
args = parser.parse_args("-d datasets/bbc/ -m models/ -p glove/glove.6B.100d.txt -n bbc".split())

In [4]:
import os 

path = os.path.join(os.getcwd(), args.dataset_path)
classes = []

logging.basicConfig(
format='%(asctime)s : %(levelname)s : %(message)s',
level=logging.INFO)

logging.info(args.dataset_path)

num_categories = 0
load_dataset = None
validator = None

if args.dataset_name in ["bbc", "20newsgroups"]:
    for file in sorted(os.listdir(path)):
        if os.path.isdir(os.path.join(path, file)):
            classes.append(file)
elif args.dataset_name in ["reuters", "ohsumed"]:
    directory = os.listdir(path)[0]
    path_to_classes = os.path.join(path, directory)
    for file in sorted(os.listdir(path_to_classes)):
        if os.path.isdir(os.path.join(path_to_classes, file)):
            classes.append(file)

print(len(classes))
            
if args.dataset_name == "bbc":
    load_dataset = load_bbc_dataset
    num_categories = 5
elif args.dataset_name == "yahoo":
    load_dataset = load_yahoo_answers_dataset
    num_categories = 10
elif args.dataset_name == "20newsgroups":
    load_dataset = load_news_groups_dataset
    num_categories = 20
elif args.dataset_name == "reuters":
    load_dataset = load_reuters_dataset
    num_categories = 91
elif args.dataset_name == "ohsumed":
    load_dataset = load_ohsumed_dataset
    num_categories = 23

2020-03-04 08:49:47,093 : INFO : datasets/bbc/


5


In [5]:
x_train, x_test, y_train, y_test = load_dataset(args.dataset_path)

han = HANModel(
    text = x_train['text'],
    labels = y_train['target'],
    num_categories = num_categories,
    pretrained_embedded_vector_path = args.pretrained_path,
    max_features = 200000,
    max_senten_len = 100,
    max_senten_num = 30,
    embedding_size = 100,
    validation_split=0.2,
    verbose=1,
    batch_size=8,
    epochs=40)

doc2vecdm = Doc2VecDMModel(
    negative=10,
    vector_size=100,
    window=5,
    workers=cores,
    min_count=1)

doc2veccbow = Doc2VecDBOWModel(
    negative=10,
    vector_size=100,
    window=5,
    workers=cores,
    min_count=1)

sif = SIFModel(
    text = x_train['text'],
    labels = y_train['target'],
    pretrained_embedded_vector_path = args.pretrained_path,
    embedding_size=100)

lda = LDAModel(
    n_components=100,
    max_features=None,
    max_df=0.95,
    min_df=0,
    epochs=10,
    cores=cores)

lsa = LSAModel(
    svd_features=100,
    n_features=None,
    n_iter=10,
    max_df=0.95,
    min_df=0)

tfidf = TfIdfModel(
    n_features=None,
    max_df=0.95,
    min_df=0)

cbow = CBOWModel(
    max_features=None,
    max_df=0.95,
    min_df=0)
benchmark_models = [cbow, tfidf, lsa, lda, sif, doc2vecdm, doc2veccbow]

if args.dataset_name in ["bbc", "20newsgroups"]:
    train_x, test_x, train_y, test_y = train_test_split(
        x_train['text'], 
        y_train['target'], 
        test_size=0.2, 
        shuffle=True)
    train_x = train_x.reset_index(drop=True)
    train_y = train_y.reset_index(drop=True)
    test_x = test_x.reset_index(drop=True)
    test_y = test_y.reset_index(drop=True)
elif args.dataset_name in ["reuters", "ohsumed"]:
    train_x, test_x, train_y, test_y = x_train['text'], x_test['text'], y_train['target'], y_test['target']   

for model in benchmark_models:
    model.build_model()
    # .values is necessary, https://github.com/dmlc/xgboost/issues/2334
    # eli5 has specific way of hanlding input data
    # by transforming it into numpy matrix we asure that features names will be correct
    model.fit(train_x.values, train_y.values)
    pred = model.predict(test_x.values, test_y.values)
    wrong_predictions = test_y.iloc[pred != test_y.values]
    print("Model: " + model.__class__.__name__)
    print("Wrong predictions: " + str(wrong_predictions.index))
    print("Ground truth: " + str(test_y[wrong_predictions.index].to_numpy()))
    print("Predictions: " + str(pred[wrong_predictions.index]))

2020-03-04 08:50:00,904 : INFO : Training classifier CBOWModel
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
2020-03-04 08:50:09,874 : INFO : Predict on classifier CBOWModel
2020-03-04 08:50:11,958 : INFO : Training classifier TfIdfModel


Model: CBOWModel
Wrong predictions: Int64Index([21, 24, 53, 55, 96, 122, 184, 253, 416, 442], dtype='int64')
Ground truth: [2 0 1 1 0 2 2 0 0 2]
Predictions: [0 4 2 2 1 4 3 2 4 0]


/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
2020-03-04 08:50:25,937 : INFO : Predict on classifier TfIdfModel
2020-03-04 08:50:28,513 : INFO : Training classifier LSAModel


Model: TfIdfModel
Wrong predictions: Int64Index([21, 122, 184, 253, 442], dtype='int64')
Ground truth: [2 2 2 0 2]
Predictions: [0 4 0 2 0]


/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
2020-03-04 08:50:36,983 : INFO : Predict on classifier LSAModel
2020-03-04 08:50:38,047 : INFO : Training classifier LDAModel


...

Model: Doc2VecDMModel
Wrong predictions: Int64Index([24, 53, 55, 122, 168, 253, 324, 419], dtype='int64')
Ground truth: [0 1 1 2 1 0 2 0]
Predictions: [2 2 0 4 2 1 0 2]


2020-03-04 08:57:52,268 : INFO : collecting all words and their counts
2020-03-04 08:57:52,269 : INFO : PROGRESS: at example #0, processed 0 words (0/s), 0 word types, 0 tags
2020-03-04 08:57:52,413 : INFO : collected 25590 word types and 5 unique tags from a corpus of 1780 examples and 660410 words
2020-03-04 08:57:52,414 : INFO : Loading a fresh vocabulary
2020-03-04 08:57:52,477 : INFO : effective_min_count=1 retains 25590 unique words (100% of original 25590, drops 0)
2020-03-04 08:57:52,478 : INFO : effective_min_count=1 leaves 660410 word corpus (100% of original 660410, drops 0)
2020-03-04 08:57:52,578 : INFO : deleting the raw counts dictionary of 25590 items
2020-03-04 08:57:52,580 : INFO : sample=0.001 downsamples 42 most-common words
2020-03-04 08:57:52,581 : INFO : downsampling leaves estimated 523028 word corpus (79.2% of prior 660410)
2020-03-04 08:57:52,657 : INFO : estimated required memory for 25590 words and 100 dimensions: 33269000 bytes
2020-03-04 08:57:52,658 : INF

2020-03-04 08:58:10,970 : INFO : EPOCH - 14 : training on 660410 raw words (524880 effective words) took 1.0s, 499908 effective words/s
2020-03-04 08:58:11,957 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-04 08:58:11,968 : INFO : worker thread finished; awaiting finish of 1 more threads
2020-03-04 08:58:11,987 : INFO : EPOCH 15 - PROGRESS: at 100.00% examples, 518486 words/s, in_qsize 0, out_qsize 1
2020-03-04 08:58:11,988 : INFO : worker thread finished; awaiting finish of 0 more threads
2020-03-04 08:58:11,989 : INFO : EPOCH - 15 : training on 660410 raw words (524824 effective words) took 1.0s, 517604 effective words/s
2020-03-04 08:58:13,004 : INFO : EPOCH 16 - PROGRESS: at 89.38% examples, 462805 words/s, in_qsize 5, out_qsize 0
2020-03-04 08:58:13,134 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-04 08:58:13,150 : INFO : worker thread finished; awaiting finish of 1 more threads
2020-03-04 08:58:13,153 : INFO : worker thre

2020-03-04 08:58:32,688 : INFO : EPOCH - 30 : training on 660410 raw words (524918 effective words) took 1.5s, 341343 effective words/s
2020-03-04 08:58:33,705 : INFO : EPOCH 31 - PROGRESS: at 83.26% examples, 436211 words/s, in_qsize 5, out_qsize 0
2020-03-04 08:58:33,888 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-04 08:58:33,895 : INFO : worker thread finished; awaiting finish of 1 more threads
2020-03-04 08:58:33,902 : INFO : worker thread finished; awaiting finish of 0 more threads
2020-03-04 08:58:33,903 : INFO : EPOCH - 31 : training on 660410 raw words (524764 effective words) took 1.2s, 437057 effective words/s
2020-03-04 08:58:34,922 : INFO : EPOCH 32 - PROGRESS: at 96.52% examples, 501907 words/s, in_qsize 3, out_qsize 0
2020-03-04 08:58:34,929 : INFO : worker thread finished; awaiting finish of 2 more threads
2020-03-04 08:58:34,943 : INFO : worker thread finished; awaiting finish of 1 more threads
2020-03-04 08:58:34,948 : INFO : worker threa

Model: Doc2VecDBOWModel
Wrong predictions: Int64Index([96, 122, 184, 190, 247, 253, 260, 267, 324, 416], dtype='int64')
Ground truth: [0 2 2 2 2 0 0 2 2 0]
Predictions: [1 4 0 0 0 4 1 0 0 4]


In [6]:
han.build_model()
# .values is necessary, https://github.com/dmlc/xgboost/issues/2334
# eli5 has specific way of hanlding input data
# by transforming it into numpy matrix we asure that features names will be correct
han.fit(train_x.values, train_y.values)
pred = han.predict(test_x.values, test_y.values)
wrong_predictions = test_y.iloc[pred != test_y.values]
print("Model: " + han.__class__.__name__)
print("Wrong predictions: " + str(wrong_predictions.index))
print("Ground truth: " + str(test_y[wrong_predictions.index].to_numpy()))
print("Predictions: " + str(pred[wrong_predictions.index]))

benchmark_models.append(han)

2020-03-04 09:00:26,620 : INFO : Training classifier HANModel
2020-03-04 09:02:16,093 : INFO : Total 27771 unique tokens.
2020-03-04 09:02:17,212 : INFO : Shape of data tensor: %s(1780, 30, 100)
2020-03-04 09:02:17,219 : INFO : Shape of labels tensor: %s(1780, 5)
2020-03-04 09:02:17,367 : INFO : Number of positive and negative reviews in traing and validation set
2020-03-04 09:02:17,369 : INFO : [0, 1, 2, 3, 4]
2020-03-04 09:02:17,505 : INFO : [339, 239, 272, 319, 255]
2020-03-04 09:02:17,508 : INFO : [79, 67, 48, 86, 76]
2020-03-04 09:02:22,466 : INFO : Total absent words are 1942 which is 6.99% of total words


Instructions for updating:
Colocations handled automatically by placer.


2020-03-04 09:02:27,423 : WARNING : From /usr/local/lib/python3.6/dist-packages/tensorflow/python/framework/op_def_library.py:263: colocate_with (from tensorflow.python.framework.ops) is deprecated and will be removed in a future version.
Instructions for updating:
Colocations handled automatically by placer.


Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


2020-03-04 09:02:51,611 : WARNING : From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:3135: calling dropout (from tensorflow.python.ops.nn_ops) with keep_prob is deprecated and will be removed in a future version.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 100)               0         
_________________________________________________________________
embedding_input (Embedding)  (None, 100, 100)          20000000  
_________________________________________________________________
bidirectional_1 (Bidirection (None, 100, 100)          45300     
_________________________________________________________________
time_distributed_1 (TimeDist (None, 100, 100)          10100     
_________________________________________________________________
attention_with_context_1 (At (None, 100)               10200     
Total params: 20,065,600
Trainable params: 65,600
Non-trainable params: 20,000,000
_________________________________________________________________
_________________________________________________________________
Layer (type)                 Output Shape              Para

2020-03-04 09:03:32,315 : WARNING : From /usr/local/lib/python3.6/dist-packages/tensorflow/python/ops/math_ops.py:3066: to_int32 (from tensorflow.python.ops.math_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.cast instead.


Train on 1424 samples, validate on 356 samples
Epoch 1/40
1424/1424 [==============================] - 128s 90ms/step - loss: 0.8416 - acc: 0.6608 - val_loss: 0.3188 - val_acc: 0.8848
Epoch 2/40
1424/1424 [==============================] - 112s 79ms/step - loss: 0.2078 - acc: 0.9389 - val_loss: 0.0985 - val_acc: 0.9747
Epoch 3/40
1424/1424 [==============================] - 118s 83ms/step - loss: 0.1281 - acc: 0.9593 - val_loss: 0.1507 - val_acc: 0.9466
Epoch 4/40
1424/1424 [==============================] - 125s 88ms/step - loss: 0.0755 - acc: 0.9761 - val_loss: 0.1558 - val_acc: 0.9607
Epoch 5/40
1424/1424 [==============================] - 123s 86ms/step - loss: 0.0860 - acc: 0.9712 - val_loss: 0.1358 - val_acc: 0.9579


2020-03-04 09:14:08,762 : INFO : Total 27771 unique tokens.
2020-03-04 09:14:11,526 : INFO : Shape of data tensor: %s(1780, 30, 100)
2020-03-04 09:14:11,531 : INFO : Shape of labels tensor: %s(0, 0)
2020-03-04 09:17:50,867 : INFO : Total absent words are 1942 which is 6.99% of total words
/usr/local/lib/python3.6/dist-packages/sklearn/model_selection/_split.py:2053: FutureWarning: You should specify a value for 'cv' instead of relying on the default value. The default value will change from 3 to 5 in version 0.22.
  warnings.warn(CV_WARNING, FutureWarning)
2020-03-04 09:18:41,189 : INFO : Predict on classifier HANModel
2020-03-04 09:18:42,021 : INFO : Total 30667 unique tokens.
2020-03-04 09:18:42,051 : INFO : Shape of data tensor: %s(445, 30, 100)
2020-03-04 09:18:42,052 : INFO : Shape of labels tensor: %s(0, 0)
2020-03-04 09:18:51,494 : INFO : Total absent words are 2346 which is 7.65% of total words


Model: HANModel
Wrong predictions: Int64Index([122, 148, 299, 416, 426, 427], dtype='int64')
Ground truth: [2 2 2 0 2 0]
Predictions: [4 0 0 4 0 2]


In [7]:
import eli5
from eli5.lime import TextExplainer
from eli5.lime.samplers import MaskingTextSampler
from sklearn.feature_extraction.text import TfidfVectorizer, CountVectorizer
from preprocess import process_string

vec = CountVectorizer(
        preprocessor=process_string, # eli5 enforce use of sklearn transformation framework
        max_features=None,
        stop_words='english')

num_samples = 15000


sampler = MaskingTextSampler(min_replace=0.5, max_replace=0.5)

from IPython.display import display

In [8]:
for index in wrong_predictions.index:
    for model in benchmark_models:
        te = TextExplainer(num_samples, vec=vec, sampler=sampler)
        te.fit(test_x[index], model.predict_proba)
        print("Model: " + model.__class__.__name__)
        print("Correct class: " + classes[test_y[index]])
        display(te.show_weights(top=20, target_names=classes))
        display(te.show_prediction(target_names=classes))

Model: CBOWModel
Correct class: politics


Model: TfIdfModel
Correct class: politics


Model: LSAModel
Correct class: politics


Model: LDAModel
Correct class: politics


Model: SIFModel
Correct class: politics


...

Model: SIFModel
Correct class: business


Model: Doc2VecDMModel
Correct class: business


Model: Doc2VecDBOWModel
Correct class: business


2020-03-04 12:54:37,155 : INFO : Total 30668 unique tokens.
2020-03-04 12:54:37,208 : INFO : Shape of data tensor: %s(15000, 30, 100)
2020-03-04 12:54:37,209 : INFO : Shape of labels tensor: %s(0, 0)
2020-03-04 12:54:44,469 : INFO : Total absent words are 2346 which is 7.65% of total words


Model: HANModel
Correct class: business
